In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import json
import os
import random
import math
import copy
import gc
from tqdm import tqdm
from glob import glob

In [4]:
DIR = "./235813_AI 기반 회의 녹취록 요약 경진대회_data/"
TRAIN_SOURCE = os.path.join(DIR, "train.json")
TEST_SOURCE = os.path.join(DIR, "test.json")

In [5]:
with open(TRAIN_SOURCE) as f:
    TRAIN_DATA = json.loads(f.read())
    
with open(TEST_SOURCE) as f:
    TEST_DATA = json.loads(f.read())

In [6]:
TRAIN_DATA

[{'id': 1000,
  'title': '제207회 완주군의회(임시회) 제 1 차 본회의회의록',
  'region': '완주',
  'num_agenda': 4,
  'context': {'AGENDA_1': {'0': '의석을 정돈하여 주시기 바랍니다. 성원이 되었으므로 제207회 완주군의회 임시회 제1차 본회의 개의를 선포합니다. 먼저 의사팀장으로부터 의회 관련 사항에 대한 보고가 있겠습니다. 의사팀장은 보고하여 주시기 바랍니다.',
    '1': '의사팀장 이은미 입니다. 의회관련 사항을 보고 드리겠습니다. 먼저 제207회 완주군의회 임시회 소집경위를 보고 드리겠습니다. 지방자치법 제45조 제2항의 규정에 의거 서남용 의원님 외 4인의 의원님으로부터 임시회 집회 요구가 있어 지난 8월6일 집회 공고를 하고 오늘 집회를 갖게 되었습니다. 다음은 의안접수 및 회부사항입니다. 먼저 의원발의 안건입니다. 완주군의회 의원 의정활동비등 지급에 관한 조례 일부개정 조례안, 완주군 향토문화유산 보호 및 관리 조례안, 완주군 싸움소 육성 지원에 관한 조례안 등 총 3건으로, 해당 상임의원회로 회부 하였습니다. 다음은 완주군수로부터 제출된 안건입니다. 삼례문화예술촌 설치 및 운영조례 일부개정 조례안 등 총 40건으로 해당 상임의원회로 회부하였습니다. 자세한 내용은 배부해 드린 유인물을 참조하여 주시기 바랍니다. 이상 보고를 마치겠습니다.'},
   'AGENDA_2': {'0': '의사팀장 수고하셨습니다. 먼저 의사일정 제1항 제207회 완주군의회 임시회 회기 결정의 건을 상정합니다. 제207회 완주군의회 임시회 회기 결정의 건에 대하여는 서남용 의원님 외 4인의 의원님이 발의한대로 8월 26일부터 9월 4일까지 10일간의 회기를 결정하고자 합니다. 의원 여러분 이의 있으십니까?',
    '1': '(『없습니다』하는 의원 있음)',
    '2': '이의가 없으므로 가결되었음을 선포합니다.'},
   'AGENDA_3': {'0': '다음은 의사일정 제2항 제2

In [12]:
TRAIN_DATA[0].keys()

dict_keys(['id', 'title', 'region', 'num_agenda', 'context', 'label'])

### List 내의 Dict 의 키 확인 및 이를 DataFrame으로 불러오기


In [18]:
train = pd.DataFrame(columns=['uid', 'title', 'region', 'context', 'summary'])
uid = 1000
for data in TRAIN_DATA:
    for agenda in data['context'].keys():
        context = ''
        for line in data['context'][agenda]:
            context += data['context'][agenda][line]
            context += ' '
        train.loc[uid, 'uid'] = uid
        train.loc[uid, 'title'] = data['title']
        train.loc[uid, 'region'] = data['region']
        train.loc[uid, 'context'] = context[:-1]
        train.loc[uid, 'summary'] = data['label'][agenda]['summary']
        uid += 1
        

In [19]:
train

uid                                 title region  \
1000  1000         제207회 완주군의회(임시회) 제 1 차 본회의회의록     완주   
1001  1001         제207회 완주군의회(임시회) 제 1 차 본회의회의록     완주   
1002  1002         제207회 완주군의회(임시회) 제 1 차 본회의회의록     완주   
1003  1003         제207회 완주군의회(임시회) 제 1 차 본회의회의록     완주   
1004  1004  제251회 완주군의회(제1차 정례회) 제1차 본 회 의 회 의 록     완주   
...    ...                                   ...    ...   
3989  3989         제327회    본회의 제2차(2020.08.26.)     음성   
3990  3990         제327회    본회의 제2차(2020.08.26.)     음성   
3991  3991         제327회    본회의 제2차(2020.08.26.)     음성   
3992  3992         제327회    본회의 제2차(2020.08.26.)     음성   
3993  3993         제327회    본회의 제2차(2020.08.26.)     음성   

                                                context  \
1000  의석을 정돈하여 주시기 바랍니다. 성원이 되었으므로 제207회 완주군의회 임시회 제...   
1001  의사팀장 수고하셨습니다. 먼저 의사일정 제1항 제207회 완주군의회 임시회 회기 결...   
1002  다음은 의사일정 제2항 제207회 완주군의회 임시회 회의록 서명의원 선출의 건을 상...   
1003  다음은 의사일정 제3항 본회의 휴회의 건을 상정합니다. 상임의원회 의정활동을 위하여...   
1004  의석을 정돈하여 주시기 바랍니다. 성원이 되었으므로 제251회 완주군의회 제1차 정...   
...                                                 ...   
3989  회계과장입니다. 회계과 소관 2020년도 주요 현안사업을 보고드리겠습니다. 보고드릴...   
3990  민원과장 김후식입니다. 민원과 소관 2020년도 주요 현안사업 추진상황을 보고드리겠...   
3991  경제과장 박세덕입니다. 경제과 2020년 주요 현안사업에 대하여 보고드리겠습니다. ...   
3992  농정과장 김기연입니다. 농정과 소관 2020년도 하반기 주요 현안사업을 보고드리겠습...   
3993  축산식품과장 송요성입니다. 축산식품과 소관 2020년도 군정주요 현안사업을 보고드리...   

                                                summary  
1000                     제207회 완주군의회 임시회 제1차 본회의 개의 선포.  
1001   제207회 완주군의회 임시회 회기는 8월 26일부터 9월 4일까지 10일간으로 가결됨.  
1002    제207회 완주군의회 임시회 회의록 서명의원으로 최등원 의원과 박웅배 의원이 선출됨.  
1003  8월 27일부터 9월 3일까지 8일간 휴회가 가결됨. 제2차 본회의는 9월 4일 오...  
1004                 제251회 완주군의회 제1차 정례회 제1차 본회의 개의 선포.  
...                                                 ...  
3989  음성읍행정복지센터 앞에 사유지 매입은 필요한 사업이기에 예산을 다시 반영해서라도 매...  
3990  공공시설물 전산화 작업시에 사유시설과 같이 협력해서 처리할 수 있도록 할 것. 지적...  
3991  용계리 지역의 땅꺼짐 현상에 대해 군 차원의 대처를 위한 고민을 해줄 것. 생극면 ...  
3992  음성군에서 생산된 쌀이 진천으로 수매하는 현상이 발생하고 있는데 음성군 브랜드를 활...  
3993  현재 저조한 길고양이 중성화사업에 적극행정을 취해줄 것. 친환경 로컬푸드 매장 조성...  

[2994 rows x 5 columns]

In [22]:
from konlpy.tag import Mecab

In [39]:
train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2994 entries, 1000 to 3993
Data columns (total 5 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   uid      2994 non-null   object
 1   title    2994 non-null   object
 2   region   2994 non-null   object
 3   context  2994 non-null   object
 4   summary  2994 non-null   object
dtypes: object(5)
memory usage: 204.9+ KB


In [54]:
train[['context']].iloc[0][0]

'의석을 정돈하여 주시기 바랍니다. 성원이 되었으므로 제207회 완주군의회 임시회 제1차 본회의 개의를 선포합니다. 먼저 의사팀장으로부터 의회 관련 사항에 대한 보고가 있겠습니다. 의사팀장은 보고하여 주시기 바랍니다. 의사팀장 이은미 입니다. 의회관련 사항을 보고 드리겠습니다. 먼저 제207회 완주군의회 임시회 소집경위를 보고 드리겠습니다. 지방자치법 제45조 제2항의 규정에 의거 서남용 의원님 외 4인의 의원님으로부터 임시회 집회 요구가 있어 지난 8월6일 집회 공고를 하고 오늘 집회를 갖게 되었습니다. 다음은 의안접수 및 회부사항입니다. 먼저 의원발의 안건입니다. 완주군의회 의원 의정활동비등 지급에 관한 조례 일부개정 조례안, 완주군 향토문화유산 보호 및 관리 조례안, 완주군 싸움소 육성 지원에 관한 조례안 등 총 3건으로, 해당 상임의원회로 회부 하였습니다. 다음은 완주군수로부터 제출된 안건입니다. 삼례문화예술촌 설치 및 운영조례 일부개정 조례안 등 총 40건으로 해당 상임의원회로 회부하였습니다. 자세한 내용은 배부해 드린 유인물을 참조하여 주시기 바랍니다. 이상 보고를 마치겠습니다.'

In [55]:
from tensorflow.keras.preprocessing.text import Tokenizer

text = train[['context']].iloc[0][0]
tok = Tokenizer()
tok.fit_on_texts([text])
encoded = tok.texts_to_sequences([text])[0]
print(encoded)
print(tok.word_index)

vocab_size = len(tok.word_index)
print('단어 집합의 크기 : ', vocab_size)

sequences = list()
for line in text.split('\n'):
  encoded = tok.texts_to_sequences([line])[0]
  #print(encoded)
  for i in range(1, len(encoded)):
    sequ = encoded[:i+1]
    #print(sequ)
    sequences.append(sequ)
print(sequences)
print('학습에 참여한 샘플 수 : %d '%len(sequences))  

[21, 22, 2, 3, 23, 24, 8, 4, 5, 25, 26, 27, 28, 6, 29, 30, 31, 32, 33, 34, 35, 36, 37, 2, 3, 38, 39, 40, 41, 42, 9, 10, 6, 8, 4, 5, 43, 9, 10, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 5, 11, 54, 55, 56, 57, 11, 58, 59, 60, 61, 62, 63, 12, 64, 7, 65, 6, 66, 13, 4, 67, 68, 69, 14, 70, 15, 1, 16, 71, 72, 7, 73, 1, 16, 74, 75, 76, 14, 1, 17, 18, 77, 19, 20, 78, 79, 12, 80, 81, 13, 82, 83, 7, 84, 15, 1, 17, 18, 85, 19, 20, 86, 87, 88, 89, 90, 91, 92, 2, 3, 93, 94, 95]
{'조례안': 1, '주시기': 2, '바랍니다': 3, '완주군의회': 4, '임시회': 5, '먼저': 6, '및': 7, '제207회': 8, '보고': 9, '드리겠습니다': 10, '집회': 11, '다음은': 12, '안건입니다': 13, '관한': 14, '일부개정': 15, '완주군': 16, '등': 17, '총': 18, '해당': 19, '상임의원회로': 20, '의석을': 21, '정돈하여': 22, '성원이': 23, '되었으므로': 24, '제1차': 25, '본회의': 26, '개의를': 27, '선포합니다': 28, '의사팀장으로부터': 29, '의회': 30, '관련': 31, '사항에': 32, '대한': 33, '보고가': 34, '있겠습니다': 35, '의사팀장은': 36, '보고하여': 37, '의사팀장': 38, '이은미': 39, '입니다': 40, '의회관련': 41, '사항을': 42, '소집경위를': 43, '지방자치법': 44, '제45조': 45, '제2항의': 46, '규정에': 47, '

In [57]:
print(max(len(i) for i in sequences)) # 가장 큰 값이 6

from tensorflow.keras.preprocessing.sequence import pad_sequences
max_len = max(len(i) for i in sequences)
psequences = pad_sequences(sequences, maxlen = max_len, padding = 'pre')    #default 는 pre
print(psequences)

123
[[ 0  0  0 ...  0 21 22]
 [ 0  0  0 ... 21 22  2]
 [ 0  0  0 ... 22  2  3]
 ...
 [ 0  0 21 ...  2  3 93]
 [ 0 21 22 ...  3 93 94]
 [21 22  2 ... 93 94 95]]


In [59]:
import numpy as np
psequences = np.array(psequences)
x = psequences[:, :-1]  #feature
y = psequences[:, -1] #label
print(x)
print(y)  # one-hot 처리 필요

from tensorflow.keras.utils import to_categorical
y = to_categorical(y, num_classes=vocab_size+1)
print(y)

[[ 0  0  0 ...  0  0 21]
 [ 0  0  0 ...  0 21 22]
 [ 0  0  0 ... 21 22  2]
 ...
 [ 0  0 21 ... 92  2  3]
 [ 0 21 22 ...  2  3 93]
 [21 22  2 ...  3 93 94]]
[22  2  3 23 24  8  4  5 25 26 27 28  6 29 30 31 32 33 34 35 36 37  2  3
 38 39 40 41 42  9 10  6  8  4  5 43  9 10 44 45 46 47 48 49 50 51 52 53
  5 11 54 55 56 57 11 58 59 60 61 62 63 12 64  7 65  6 66 13  4 67 68 69
 14 70 15  1 16 71 72  7 73  1 16 74 75 76 14  1 17 18 77 19 20 78 79 12
 80 81 13 82 83  7 84 15  1 17 18 85 19 20 86 87 88 89 90 91 92  2  3 93
 94 95]
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 0. ... 0. 0. 1.]]


In [60]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.layers import  Embedding, Dense, SimpleRNN, LSTM, Input
from tensorflow.keras.models import Sequential, Model

# function api
# input = Input(shape=(50,1))
# lstm_layer=LSTM(20, activation='tanh')(input)
# x = Dense(20, activation='relu')(lstm_layer)
# output = Dense(1, activation='softmax')(x)
# model = Model(input, output)

# Sequential api
model = Sequential()
model.add(Embedding(vocab_size+1, 32, input_length=max_len -1))
model.add(LSTM(32, activation='tanh'))
#model.add(SimpleRNN(32, activation='tanh'))
model.add(Dense(32, activation='relu'))
model.add(Dense(vocab_size + 1, activation='softmax'))
#print(model.summary())

#compile
model.compile(loss = 'categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.fit(x, y, epochs=200, verbose=2)
print(model.evaluate(x, y))


Epoch 1/200
4/4 - 3s - loss: 4.5654 - accuracy: 0.0082
Epoch 2/200
4/4 - 0s - loss: 4.5623 - accuracy: 0.0328
Epoch 3/200
4/4 - 0s - loss: 4.5603 - accuracy: 0.0328
Epoch 4/200
4/4 - 0s - loss: 4.5576 - accuracy: 0.0328
Epoch 5/200
4/4 - 0s - loss: 4.5548 - accuracy: 0.0328
Epoch 6/200
4/4 - 0s - loss: 4.5514 - accuracy: 0.0328
Epoch 7/200
4/4 - 0s - loss: 4.5473 - accuracy: 0.0328
Epoch 8/200
4/4 - 0s - loss: 4.5420 - accuracy: 0.0328
Epoch 9/200
4/4 - 0s - loss: 4.5329 - accuracy: 0.0328
Epoch 10/200
4/4 - 0s - loss: 4.5208 - accuracy: 0.0328
Epoch 11/200
4/4 - 0s - loss: 4.5004 - accuracy: 0.0328
Epoch 12/200
4/4 - 0s - loss: 4.4774 - accuracy: 0.0410
Epoch 13/200
4/4 - 0s - loss: 4.4483 - accuracy: 0.0410
Epoch 14/200
4/4 - 0s - loss: 4.4226 - accuracy: 0.0492
Epoch 15/200
4/4 - 0s - loss: 4.3907 - accuracy: 0.0410
Epoch 16/200
4/4 - 0s - loss: 4.3566 - accuracy: 0.0410
Epoch 17/200
4/4 - 0s - loss: 4.3159 - accuracy: 0.0410
Epoch 18/200
4/4 - 0s - loss: 4.2734 - accuracy: 0.0410
E

Epoch 147/200
4/4 - 0s - loss: 1.3297 - accuracy: 0.8033
Epoch 148/200
4/4 - 0s - loss: 1.3222 - accuracy: 0.8115
Epoch 149/200
4/4 - 0s - loss: 1.3114 - accuracy: 0.8115
Epoch 150/200
4/4 - 0s - loss: 1.2997 - accuracy: 0.8197
Epoch 151/200
4/4 - 0s - loss: 1.2872 - accuracy: 0.8115
Epoch 152/200
4/4 - 0s - loss: 1.2742 - accuracy: 0.8115
Epoch 153/200
4/4 - 0s - loss: 1.2687 - accuracy: 0.7951
Epoch 154/200
4/4 - 0s - loss: 1.2567 - accuracy: 0.8033
Epoch 155/200
4/4 - 0s - loss: 1.2438 - accuracy: 0.8361
Epoch 156/200
4/4 - 0s - loss: 1.2364 - accuracy: 0.8361
Epoch 157/200
4/4 - 0s - loss: 1.2255 - accuracy: 0.8443
Epoch 158/200
4/4 - 0s - loss: 1.2211 - accuracy: 0.8443
Epoch 159/200
4/4 - 0s - loss: 1.2087 - accuracy: 0.8443
Epoch 160/200
4/4 - 0s - loss: 1.1963 - accuracy: 0.8443
Epoch 161/200
4/4 - 0s - loss: 1.1885 - accuracy: 0.8443
Epoch 162/200
4/4 - 0s - loss: 1.1775 - accuracy: 0.8770
Epoch 163/200
4/4 - 0s - loss: 1.1647 - accuracy: 0.8607
Epoch 164/200
4/4 - 0s - loss: 

In [61]:
def sequence_generation(model, t, current_word, n):
  init_word = current_word
  sentence = ''
  for _ in range(n):
    encoded = t.texts_to_sequences([current_word])[0]
    encoded = pad_sequences([encoded], maxlen=max_len-1, padding='pre')
    #print(encoded)
    result = np.argmax(model.predict(encoded))
    #print(result)
    for word, index in t.word_index.items():
      #print('word:', word, ', index:', index)
      if index == result:
        break
    current_word = current_word + ' ' + word
    sentence = sentence+ ' ' + word
  sentence = init_word + sentence
  return sentence

In [63]:
print(sequence_generation(model, tok, '임시회', 10))

임시회 정돈하여 주시기 바랍니다 성원이 되었으므로 제207회 완주군의회 제1차 본회의 개의를
